In [1]:
import requests
import json
import asyncio
import time
import websockets
import datetime
import numpy as np
import pandas as pd
import polars as pl
import matplotlib.pyplot as plt
import ast
from datetime import datetime, timedelta
import math

In [2]:
def query_polymarket(limit = 500):
    """
    input: number of contracts that want to be pulled
    output: returns lists of polygon market objects
    
    notes: polymarket has limit of 100 market objects per call, so we split the limit by 100 
    """
    offset = 0
    num_offsets = math.ceil(limit/100)
    i = 0
    output = []
    
    while i < num_offsets:
        params = {'closed': 'False',
                 'limit':100,
                 'offset' : offset}
        r = requests.get("https://gamma-api.polymarket.com/events", params = params)
        if r.status_code == 200:
            output+=r.json()
            i += 1
            offset += 100
        else:
            break
            

    return output
query = query_polymarket()

In [17]:
def landing_data(name):
    params = {'closed': 'False',
              'limit':500,
              'ascending': False,
              'order':name}

    r = requests.get("https://gamma-api.polymarket.com/events", params = params)
    if r.status_code == 200:
        markets =  r.json()
    else:
        print('oh no')
        return
    return [(market['title'], market[name]) for market in markets]

#liquidity, volume


In [3]:
political_tags = np.array(['Trump','Kamala'])

def find_markets(tags, markets):
    """
    input: input is a list of tags that are looked for and a list of polygon market objects
    output: return a lists of polygon market objects
    """
    filtered_markets = {}
    for market in markets:
        question = market['title'].split()
        if True in [i in question for i in tags]:
            filtered_markets[market['id']] = market
    return filtered_markets
political_markets = find_markets(political_tags,query)
len(political_markets)

67

In [57]:
def most_uncertain_contract(markets):
    """
    input: list of polymarket markets objects
    output: for each market, returns the most uncertain polymarket YES contract object in the market
    """
    output = []
    for market in markets:
        kept_contract = -1
        uncertainty = float('inf')
        for contract in market['markets']:
            p_yes = [float(value) for value in ast.literal_eval(contract['outcomePrices'])][0]
            if abs(p_yes-.5) < uncertainty:
                uncertainty = abs(p_yes-.5)
                kept_contract = contract
        output.append(kept_contract)
    return output
political_contracts = most_uncertain_contract(list(political_markets.values()))

In [104]:
def split_times(start, end, freq = 'hourly'):
    output = []
    cap = 360
    current_time = start
    next_time = start
    while True:
        next_time = current_time + timedelta(hours = cap)
        if next_time >= end:
            output.append((int(time.mktime(current_time.timetuple())), int(time.mktime(end.timetuple()))))
            return output
        output.append((int(time.mktime(current_time.timetuple())), int(time.mktime(next_time.timetuple()))))
        current_time = next_time
    return

In [145]:
def query_data(contracts,start, end):
    """
    input: list of polymarket contracts objects
    output: list tuples with polymarket objects, time series data of 4 hour interval data for a week
    
    time series data: stored as dictionary with key 't' as time and 'p' as contract time
    """
    output = []
    splitpoints = split_times(start,end) # needed in since the limit of api calls is 361 
    ids = dict([(tuple(ast.literal_eval(contract['clobTokenIds'])), contract) for contract in political_contracts])
    for clobTokens in ids.keys():
        for token in clobTokens:
            output_time = []
            output_p =[]
            for t in splitpoints:
                # print(t, [datetime.fromtimestamp(t[0]).strftime('%Y-%m-%d %H:%M:%S')])
                params = {
                "market": int(token),
                "startTs": t[0],
                "endTs": t[1],
                "fidelity": 60  # Fidelity in minutes (example: 60 means hourly data)
                }
                r = requests.get("https://clob.polymarket.com/prices-history",params = params)
                if r.status_code == 200:
                    data = r.json()['history']
                    output_time += [datetime.fromtimestamp(item['t']).strftime('%Y-%m-%d %H:%M:%S') for item in data]
                    output_p += [item['p'] for item in data]
                    # print(output_p)
                else:
                    print(f"Error: {r.status_code} - {r.text}")
                    raise valueError
            
            else:
                data = {'t': output_time, 'p' :output_p}
                output.append((ids[clobTokens], data))
                break
            
    return output

now = datetime.now()
past = current_time - timedelta(days=30)

time_data = query_data(political_contracts, past, now)

In [146]:
time_data

[({'id': '253591',
   'question': 'Will Donald Trump win the 2024 US Presidential Election?',
   'conditionId': '0xdd22472e552920b8438158ea7238bfadfa4f736aa4cee91a6b86c39ead110917',
   'slug': 'will-donald-trump-win-the-2024-us-presidential-election',
   'resolutionSource': '',
   'endDate': '2024-11-04T12:00:00Z',
   'liquidity': '3424111.00143',
   'startDate': '2024-01-04T22:58:00Z',
   'fee': '20000000000000000',
   'image': 'https://polymarket-upload.s3.us-east-2.amazonaws.com/will-donald-trump-win-the-2024-us-presidential-election-c83f01bb-5089-4222-9347-3f12673b6a48.png',
   'icon': 'https://polymarket-upload.s3.us-east-2.amazonaws.com/will-donald-trump-win-the-2024-us-presidential-election-c83f01bb-5089-4222-9347-3f12673b6a48.png',
   'description': 'This market will resolve to “Yes” if Donald J. Trump wins the 2024 US Presidential Election. Otherwise, this market will resolve to “No.”\n\nThe resolution source for this market is the Associated Press, Fox News, and NBC. This mar

In [147]:
import pickle
with open('time_data.pickle', 'wb') as f:
    pickle.dump(time_data, f)